## get_obs_paths

The purpose of this notebook is to read in a CSV table containing a column of PACS obsids, and add a column containing the path to a FITS file corresponding to each observation, where available. This is useful if you have a folder full of data downloaded from the *Herschel* Science Archive (HSA) but don't know specifically where the observation you're looking for is located. In particular, the table produced by this notebook can be used as input to the disc modelling code `pacs_model_batch.py`.

The notebook assumes that the data have been downloaded from HSA and placed in some specified root directory, and that the file structure has not been altered following the download &#150; the obsid, level and processing method of a particular image are inferred from its path. An alternative method, independent of the file structure, would be to open *all* FITS files found and extract the relevant information, but this would be much more time-consuming.

It is also expected that the input table includes columns `wave` and `star_jy`, containing wavelengths and predicted stellar fluxes for each system at 70/100 μm (i.e. there are at least two rows for each system). For the final output table, the appropriate row will be selected, given the wavelength of the obsid as determined from the FITS file.

### Setup

In [1]:
import pandas as pd
import numpy as np
from astropy.io import fits
from pathlib import Path

In [2]:
#don't truncate path strings when displaying them in a DataFrame
pd.set_option('display.max_colwidth', -1)

#display the full tables
pd.set_option('display.max_rows', None)

### Obtain a list of relevant images

This is achieved by walking recursively through all directories contained in `rootdir` and appending the paths that match one of the specified patterns to a list. Here, we look for level 2 and level 2.5 high-pass filtered "blue" (70/100 μm) images.

In [3]:
#all data should be somewhere inside this directory
rootdir = '/data/wyatt_archive/gkennedy/hsa/auto'

#look for files matching these patterns
patterns = ['*/level2_5/HPPHPFMAPB/*.fits.gz*/', '*/level2/HPPPMAPB/*.fits.gz']

In [4]:
#get the paths of all desired maps within rootdir

path = []
obsid_from_path = []
mtime = []
obs_wave = []
level = []

#match each of the appropriate patterns
for pattern in patterns:
    
    for p in Path(rootdir).rglob(pattern):

        full_path = p.resolve()
        path.append(str(full_path))

        #need to go three levels up to get the obsid, given the file structure provided by HSA
        obsid_from_path.append(int(full_path.parents[2].name))
        
        #the processing level can be determined from the directory two levels up
        level.append(full_path.parents[1].name)

        #append the last modification time, so that we can find the most up-to-date file if duplicates are found
        mtime.append(p.lstat().st_mtime)

        #extract observation wavelength from FITS file
        with fits.open(str(full_path))as datafile:
            obs_wave.append(int(datafile[0].header['WAVELNTH']))

In [5]:
#store the results in a DataFrame, so that we can easily join them onto the provided CSV table
df_paths = pd.DataFrame({'obsid': obsid_from_path, 'obs_wave': obs_wave, 'level': level, 'path': path, 'mtime': mtime},
                        columns = ['obsid', 'obs_wave', 'level', 'path', 'mtime'])

#sort by obsid and then level, with the highest levels and newest files (i.e. largest mtimes) at the top
df_paths.sort_values(by = ['obsid', 'level', 'mtime'], ascending = [True, False, False], inplace = True)

In [6]:
#if multiple images were found for a particular obsid, keep those with the
#highest level of processing, and from those, only the most recently modified file
df_paths.drop_duplicates(subset = ['obsid'], keep = 'first', inplace = True)

#modification times were only necessary for sorting; drop these now
df_paths.drop(['mtime'], axis = 1, inplace = True)

In [7]:
#look at the final path table
df_paths

obsid  obs_wave     level  \
8     1342186612  70        level2_5   
9     1342186619  70        level2_5   
5     1342187075  100       level2_5   
2046  1342187141  100       level2     
2047  1342187142  70        level2     
6     1342187145  100       level2_5   
2035  1342187248  100       level2     
2048  1342187255  100       level2     
2044  1342187338  70        level2     
2045  1342187342  70        level2     
2036  1342187364  100       level2     
2037  1342187365  100       level2     
2038  1342187805  100       level2     
2039  1342187806  100       level2     
2040  1342187807  100       level2     
2041  1342187808  100       level2     
2042  1342187835  100       level2     
2043  1342188072  100       level2     
2049  1342188366  70        level2     
2050  1342188367  70        level2     
2051  1342188368  70        level2     
10    1342188369  70        level2_5   
11    1342188370  70        level2_5   
12    1342188371  70        level2_5   
13    1342188372  70        level2_5   
14    1342188377  70        level2_5   
2052  1342188473  70        level2     
15    1342188484  70        level2_5   
2053  1342188485  70        level2     
16    1342188506  70        level2_5   
17    1342188507  70        level2_5   
18    1342188514  70        level2_5   
2054  1342188515  70        level2     
19    1342188516  70        level2_5   
20    1342188517  70        level2_5   
21    1342188518  70        level2_5   
2055  1342188519  70        level2     
2056  1342188847  70        level2     
2057  1342188848  70        level2     
2058  1342188853  70        level2     
22    1342188854  70        level2_5   
2059  1342188879  70        level2     
23    1342188884  70        level2_5   
24    1342188885  70        level2_5   
2060  1342188886  70        level2     
25    1342188887  70        level2_5   
26    1342189150  70        level2_5   
2061  1342189163  70        level2     
2062  1342189193  70        level2     
2063  1342189210  70        level2     
27    1342189365  70        level2_5   
2064  1342189366  70        level2     
28    1342189367  70        level2_5   
2065  1342189368  70        level2     
2066  1342189387  70        level2     
2067  1342189394  70        level2     
29    1342189592  70        level2_5   
2068  1342189656  70        level2     
30    1342189657  70        level2_5   
31    1342189658  70        level2_5   
32    1342189659  70        level2_5   
33    1342190306  70        level2_5   
34    1342190345  70        level2_5   
35    1342190346  70        level2_5   
2069  1342190967  70        level2     
36    1342191014  70        level2_5   
37    1342191015  70        level2_5   
38    1342191016  70        level2_5   
39    1342191017  70        level2_5   
40    1342191018  70        level2_5   
606   1342191102  100       level2_5   
1787  1342191104  70        level2_5   
228   1342192757  100       level2_5   
41    1342192759  70        level2_5   
607   1342192760  100       level2_5   
608   1342192775  100       level2_5   
229   1342193038  100       level2_5   
230   1342193040  100       level2_5   
231   1342193042  100       level2_5   
232   1342193046  100       level2_5   
2070  1342193054  70        level2     
609   1342193057  100       level2_5   
233   1342193059  100       level2_5   
234   1342193061  100       level2_5   
235   1342193064  100       level2_5   
236   1342193068  100       level2_5   
237   1342193105  100       level2_5   
238   1342193107  100       level2_5   
239   1342193109  100       level2_5   
42    1342193111  70        level2_5   
610   1342193112  100       level2_5   
240   1342193115  100       level2_5   
611   1342193117  100       level2_5   
241   1342193123  100       level2_5   
2071  1342193125  70        level2     
2072  1342193130  70        level2     
2073  1342193131  70        level2     
2074  1342193134  70        level2     
2075  1342193135  70        level2     
2076  13421

### Read in the CSV table 

In [8]:
csv_filename = 'input/obs_list.csv'
df_in = pd.read_csv(csv_filename)

In [9]:
#look at the input table
df_in

obsid                      xid      dist_pc   filter  wave  \
0     1342212471  HD 224953                15.328020    PACS100  100    
1     1342212471  HD 224953                15.328020    PACS70   70     
2     1342212800  * 85 Peg                 12.647086    PACS100  100    
3     1342212800  * 85 Peg                 12.647086    PACS70   70     
4     1342221120  HD 225213                4.339901     PACS100  100    
5     1342221120  HD 225213                4.339901     PACS70   70     
6     1342188367  HD 105                   38.476337    PACS100  100    
7     1342188367  HD 105                   38.476337    PACS70   70     
8     1342237872  HD 123                   21.477663    PACS100  100    
9     1342237872  HD 123                   21.477663    PACS70   70     
10    1342233625  HD 142                   25.713551    PACS100  100    
11    1342233625  HD 142                   25.713551    PACS70   70     
12    1342213512  HD 166                   13.768415    PACS100  100    
13    1342213512  HD 166                   13.768415    PACS70   70     
14    1342212461  GJ 1002                  4.849345     PACS100  100    
15    1342212461  GJ 1002                  4.849345     PACS70   70     
16    1342188366  HD 203                   39.385585    PACS100  100    
17    1342188366  HD 203                   39.385585    PACS70   70     
18    1342199875  * 6 Cet                  17.989818    PACS100  100    
19    1342199875  * 6 Cet                  17.989818    PACS70   70     
20    1342212469  * tet Scl                21.648021    PACS100  100    
21    1342212469  * tet Scl                21.648021    PACS70   70     
22    1342223979  V* LN Peg                44.088212    PACS100  100    
23    1342223979  V* LN Peg                44.088212    PACS70   70     
24    1342223913  HD 1100                  157.611865   PACS100  100    
25    1342223913  HD 1100                  157.611865   PACS70   70     
26    1342212467  G 158-50                 4.986785     PACS100  100    
27    1342212467  G 158-50                 4.986785     PACS70   70     
28    1342204272  HD 1237                  17.564845    PACS100  100    
29    1342204272  HD 1237                  17.564845    PACS70   70     
30    1342213223  BD+40 45                 14.686444    PACS100  100    
31    1342213223  BD+40 45                 14.686444    PACS70   70     
32    1342213948  * sig And                41.322314    PACS100  100    
33    1342213948  * sig And                41.322314    PACS70   70     
34    1342213942  V* GX And                3.562647     PACS100  100    
35    1342213942  V* GX And                3.562647     PACS70   70     
36    1342188369  HD 1466                  42.955326    PACS100  100    
37    1342188369  HD 1466                  42.955326    PACS70   70     
38    1342223911  HD 1461                  23.245002    PACS100  100    
39    1342223911  HD 1461                  23.245002    PACS70   70     
40    1342225479  HD 1502                  191.957002   PACS100  100    
41    1342225479  HD 1502                  191.957002   PACS70   70     
42    1342198529  * zet Tuc                8.586639     PACS100  100    
43    1342198529  * zet Tuc                8.586639     PACS70   70     
44    1342212739  * 9 Cet                  21.285653    PACS100  100    
45    1342212739  * 9 Cet                  21.285653    PACS70   70     
46    1342212623  LP 881-64                7.723797     PACS100  100    
47    1342212623  LP 881-64                7.723797     PACS70   70     
48    1342220764  * kap Phe                23.809524    PACS100  100    
49    1342220764  * kap Phe                23.809524    PACS70   70     
50    1342237339  HD 2475                  32.195750    PACS100  100    
51    1342237339  HD 2475                  32.195750    PACS70   70     
52    1342225487  IRAS F00267+0935         505.356782   PACS100  100    
53    1342225487  IRAS F00267+0935         505.356782   PACS70   70  

### Left join the path table onto the input table

The rows of the resulting table will be the same as that of the input table, with a path column added.

In [10]:
merged = pd.merge(df_in, df_paths, how = 'left', on = 'obsid')

In [11]:
#look at the merged table
merged

obsid                      xid      dist_pc   filter  wave  \
0     1342212471  HD 224953                15.328020    PACS100  100    
1     1342212471  HD 224953                15.328020    PACS70   70     
2     1342212800  * 85 Peg                 12.647086    PACS100  100    
3     1342212800  * 85 Peg                 12.647086    PACS70   70     
4     1342221120  HD 225213                4.339901     PACS100  100    
5     1342221120  HD 225213                4.339901     PACS70   70     
6     1342188367  HD 105                   38.476337    PACS100  100    
7     1342188367  HD 105                   38.476337    PACS70   70     
8     1342237872  HD 123                   21.477663    PACS100  100    
9     1342237872  HD 123                   21.477663    PACS70   70     
10    1342233625  HD 142                   25.713551    PACS100  100    
11    1342233625  HD 142                   25.713551    PACS70   70     
12    1342213512  HD 166                   13.768415    PACS100  100    
13    1342213512  HD 166                   13.768415    PACS70   70     
14    1342212461  GJ 1002                  4.849345     PACS100  100    
15    1342212461  GJ 1002                  4.849345     PACS70   70     
16    1342188366  HD 203                   39.385585    PACS100  100    
17    1342188366  HD 203                   39.385585    PACS70   70     
18    1342199875  * 6 Cet                  17.989818    PACS100  100    
19    1342199875  * 6 Cet                  17.989818    PACS70   70     
20    1342212469  * tet Scl                21.648021    PACS100  100    
21    1342212469  * tet Scl                21.648021    PACS70   70     
22    1342223979  V* LN Peg                44.088212    PACS100  100    
23    1342223979  V* LN Peg                44.088212    PACS70   70     
24    1342223913  HD 1100                  157.611865   PACS100  100    
25    1342223913  HD 1100                  157.611865   PACS70   70     
26    1342212467  G 158-50                 4.986785     PACS100  100    
27    1342212467  G 158-50                 4.986785     PACS70   70     
28    1342204272  HD 1237                  17.564845    PACS100  100    
29    1342204272  HD 1237                  17.564845    PACS70   70     
30    1342213223  BD+40 45                 14.686444    PACS100  100    
31    1342213223  BD+40 45                 14.686444    PACS70   70     
32    1342213948  * sig And                41.322314    PACS100  100    
33    1342213948  * sig And                41.322314    PACS70   70     
34    1342213942  V* GX And                3.562647     PACS100  100    
35    1342213942  V* GX And                3.562647     PACS70   70     
36    1342188369  HD 1466                  42.955326    PACS100  100    
37    1342188369  HD 1466                  42.955326    PACS70   70     
38    1342223911  HD 1461                  23.245002    PACS100  100    
39    1342223911  HD 1461                  23.245002    PACS70   70     
40    1342225479  HD 1502                  191.957002   PACS100  100    
41    1342225479  HD 1502                  191.957002   PACS70   70     
42    1342198529  * zet Tuc                8.586639     PACS100  100    
43    1342198529  * zet Tuc                8.586639     PACS70   70     
44    1342212739  * 9 Cet                  21.285653    PACS100  100    
45    1342212739  * 9 Cet                  21.285653    PACS70   70     
46    1342212623  LP 881-64                7.723797     PACS100  100    
47    1342212623  LP 881-64                7.723797     PACS70   70     
48    1342220764  * kap Phe                23.809524    PACS100  100    
49    1342220764  * kap Phe                23.809524    PACS70   70     
50    1342237339  HD 2475                  32.195750    PACS100  100    
51    1342237339  HD 2475                  32.195750    PACS70   70     
52    1342225487  IRAS F00267+0935         505.356782   PACS100  100    
53    1342225487  IRAS F00267+0935         505.356782   PACS70   70  

In [12]:
#were there any systems on the list that we couldn't find an image for?
n_missing_image = len(merged[pd.isna(merged.path)])
print(("Some" if n_missing_image else "No") + " missing images.")

No missing images.


### Clean up the final table

In [13]:
#select appropriate wavelength and remove unnecessary columns
merged = merged[(merged.wave == merged.obs_wave)][['obsid', 'xid', 'dist_pc', 'wave',
                                                   'star_jy', 'raj2000', 'dej2000', 'level', 'path']]

In [14]:
#convert the stellar flux into mJy, as expected by pacs_model.py
merged.star_jy *= 1000
merged.rename(columns = {"star_jy": "star_mjy"}, inplace = True)

In [15]:
#if we end up with multiple entries for one star in the same obsid, place NaN distances at the bottom
merged.sort_values(by = ['obsid', 'xid', 'dist_pc'], inplace = True)

#and then keep only the first entry for these stars
merged.drop_duplicates(subset = ['obsid', 'xid'], keep = 'first', inplace = True)

In [16]:
#take a look at the result
merged

obsid                      xid      dist_pc  wave     star_mjy  \
753   1342186612  * bet Pic                19.440124    70    30.683300     
2388  1342187075  * del Pav                6.108362     100   74.044400     
2564  1342187145  HD 211415                14.016812    100   12.715700     
2616  1342187255  * 51 Peg                 15.607929    100   10.378100     
1049  1342187338  2MASS J08431857-7905181 NaN           70    5.944570      
1289  1342187342  V* TW Hya                59.523810    70    2.141890      
1544  1342187807  * alf02 CVn              35.198874    100   20.180200     
17    1342188366  HD 203                   39.385585    70    6.407560      
7     1342188367  HD 105                   38.476337    70    3.022420      
81    1342188368  BPM 16228                41.160733    70    1.237650      
37    1342188369  HD 1466                  42.955326    70    2.865540      
2697  1342188370  * eta Tuc                47.438330    70    6.962280      
269   1342188371  * eps Hyi                46.554935    70    15.351700     
255   1342188372  EXO 0235.2-5216          38.846568    70    1.207670      
201   1342188377  V* DK Cet                40.783034    70    2.192270      
59    1342188484  HD 3221                  44.498832    70    2.445420      
789   1342188506  V* AO Men                39.262647    70    1.926240      
793   1342188507  HD 44627                 50.200803    70    1.486200      
1205  1342188514  HD 298936                53.350405    70    1.232600      
1253  1342188515  V* CE Ant                34.029000    70    2.344750      
1437  1342188516  TWA 23                   55.670608    70    1.083450      
1459  1342188517  V* V1249 Cen             53.110975    70    1.295660      
1503  1342188518  V* V1252 Cen             57.597051    70    0.449589      
1307  1342188847  HD 97048                NaN           70    1.456980      
1425  1342188848  V* DX Cha                108.389334   70    7.587520      
1351  1342188853  HD 100453                102.774923   70    2.387370      
1501  1342188854  TWA 16                  NaN           70    0.752055      
1353  1342188879  HD 100546                109.170306   70    2.842350      
1031  1342188884  V* EH Cha               NaN           70    0.220925      
859   1342188885  HD 55279                 63.411541    70    0.764734      
827   1342188886  HD 53842                 56.022409    70    2.447150      
55    1342188887  2MASS J00313267-6257297  41.407867    70    12.217000     
277   1342189150  BD+05 378                44.437334    70    1.584910      
1311  1342189163  TYC 7201-27-1            46.080613    70    2.526030      
227   1342189193  TYC 1777-1480-1          39.261877    70    2.659040      
237   1342189210  V* AG Tri                41.084634    70    1.336010      
995   1342189365  2MASS J08361072-7908183  98.495967    70    0.087438      
1033  1342189367  HD 75505                 94.966762    70    1.282530      
1027  1342189368  2MASS J08413030-7853064 NaN           70    0.097851      
1067  1342189387  V* EP Cha               NaN           70    1.765270      
57    1342189394  * bet03 Tuc              45.558087    70    8.027560      
1831  1342189592  2MASS J15355780-2324046 NaN           70    0.168157      
1879  1342189656  HD 142315                147.710487   70    1.784360      
1883  1342189657  2MASS J15562477-2225552  141.175142   70    0.105283      
1877  1342189658  HD 142097                140.920493   70    1.331180      
1851  1342189659  2MASS J15441334-2522590 NaN           70    0.248523      
479   1342190306  V* T Tau                 144.320970   70    3.049340      
491   1342190345  HD 285778                120.078291   70    0.375347      
511   1342190346  HBC 392                  140.217056   70    0.158735      
409   1342191014  2MASS J03542950+3203013  291.002212   70    0.164560      
413   1342191015  2MASS J03543556+2537111  277.993995   70    0.034291      
423   1

### Save the output

In [17]:
#'input' since this will likely be used as input to pacs_model_batch.py!
output_file = 'input/obs_path_list.csv'

In [18]:
#no need to save the indices
merged.to_csv(output_file, index = False)

## Some miscellaneous experimentation below...

In [19]:
#try joining the other way round (i.e. see which systems we have data for, but weren't in the input list)
missing = pd.merge(df_paths, df_in, how = 'left', on = 'obsid')
missing[pd.isna(missing.xid)]['obsid']

2       1342186619
5       1342187141
6       1342187142
9       1342187248
16      1342187364
17      1342187365
18      1342187805
19      1342187806
22      1342187808
23      1342187835
24      1342188072
41      1342188473
44      1342188485
59      1342188519
90      1342189366
117     1342190967
130     1342191104
185     1342193136
192     1342193140
209     1342193159
214     1342193165
223     1342193511
232     1342193528
241     1342194065
244     1342195352
251     1342195466
258     1342195577
273     1342195698
302     1342196107
307     1342196117
322     1342196755
327     1342196783
332     1342196789
355     1342197679
358     1342197703
401     1342198547
412     1342198909
465     1342203668
500     1342204266
521     1342205159
526     1342205165
543     1342205974
546     1342205978
565     1342206317
566     1342206320
571     1342206328
640     1342208853
645     1342208861
670     1342209061
697     1342209377
706     1342209466
713     1342209482
714     1342

In [20]:
#look at obsids with more than one star listed
merged[merged.obsid.isin(merged.obsid.value_counts().loc[lambda x: x>1].reset_index()['index'])].sort_values(by = ['obsid','xid'])

obsid                      xid      dist_pc  wave     star_mjy  \
1726  1342224848  * alf Cen A              1.324837     100   1706.320000   
1724  1342224848  * alf Cen B              1.254831     100   725.506000    
561   1342224850  * c Eri                  29.429076    70    12.128200     
563   1342224850  GJ 3305                 NaN           70    3.248110      
2266  1342259238  2MASS J19145690+4645432 NaN           100   0.000282      
2268  1342259238  2MASS J19145735+4645452  805.282654   100   0.004726      
2328  1342259242  2MASS J19453253+4814004  1482.359917  100   0.002900      
2330  1342259242  2MASS J19453257+4813533 NaN           100   0.000521      

         raj2000    dej2000     level  \
1726  219.902058 -60.833993  level2_5   
1724  219.896096 -60.837528  level2_5   
561   69.400551  -2.473550   level2_5   
563   69.406045  -2.491353   level2_5   
2266  288.737016  46.762064  level2_5   
2268  288.738956  46.762581  level2_5   
2328  296.385541  48.233434  level2_5   
2330  296.385673  48.231382  level2_5   

                                                                                                                                                        path  
1726  /data/wyatt_archive/gkennedy/hsa/auto/AIOURL278293731/1342224848/level2_5/HPPHPFMAPB/hpacs_25HPPHPFMAPB_green_1439_m6050_00_v1.0_1471788061502.fits.gz  
1724  /data/wyatt_archive/gkennedy/hsa/auto/AIOURL278293731/1342224848/level2_5/HPPHPFMAPB/hpacs_25HPPHPFMAPB_green_1439_m6050_00_v1.0_1471788061502.fits.gz  
561   /data/wyatt_archive/gkennedy/hsa/auto/AIOURL278293034/1342224850/level2_5/HPPHPFMAPB/hpacs_25HPPHPFMAPB_blue_0438_m0229_00_v1.0_1471787734315.fits.gz   
563   /data/wyatt_archive/gkennedy/hsa/auto/AIOURL278293034/1342224850/level2_5/HPPHPFMAPB/hpacs_25HPPHPFMAPB_blue_0438_m0229_00_v1.0_1471787734315.fits.gz   
2266  /data/wyatt_archive/gkennedy/hsa/auto/AIOURL278294349/1342259238/level2_5/HPPHPFMAPB/hpacs_25HPPHPFMAPB_green_1915_p4646_00_v1.0_1472361590994.fits.gz  
2268  /data/wyatt_archive/gkennedy/hsa/auto/AIOURL278294349/1342259238/level2_5/HPPHPFMAPB/hpacs_25HPPHPFMAPB_green_1915_p4646_00_v1.0_1472361590994.fits.gz  
2328  /data/wyatt_archive/gkennedy/hsa/auto/AIOURL278294351/1342259242/level2_5/HPPHPFMAPB/hpacs_25HPPHPFMAPB_green_1946_p4814_00_v1.0_1472362234898.fits.gz  
2330  /data/wyatt_archive/gkennedy/hsa/auto/AIOURL278294351/1342259242/level2_5/HPPHPFMAPB/hpacs_25HPPHPFMAPB_green_1946_p4814_00_v1.0_1472362234898.fits.gz